# **Predicting Tarmac Delays**

This notebook will focus purely on exploratory data analysis and modeling. The following data was scraped and merged from two different sources: *Bureau of Transportation Statistics* and *WeatherUnderground*. For more information on how I scraped this data, please refer to the **Data Collection (Web Scraping).ipynb** notebook.

In [14]:
import pandas as pd
import numpy as np
import statsmodels.api as sm
import statsmodels.formula.api as smf
import patsy
import datetime
import seaborn as sns
import matplotlib.pyplot as plt
import plotly
import sklearn
from sklearn.linear_model import LinearRegression, Lasso, LassoCV, Ridge, RidgeCV
from sklearn.linear_model import RidgeCV
from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import PolynomialFeatures
from sklearn.pipeline import make_pipeline
from sklearn import metrics
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from chart_studio.plotly import plot, iplot as py
import plotly.graph_objects as go
from plotly.offline import iplot, init_notebook_mode

import cufflinks
cufflinks.go_offline(connected=True)
init_notebook_mode(connected=True)

%matplotlib inline

In [2]:
def configure_plotly_browser_state():
  import IPython
  display(IPython.core.display.HTML('''
        <script src="/static/components/requirejs/require.js"></script>
        <script>
          requirejs.config({
            paths: {
              base: '/static/base',
              plotly: 'https://cdn.plot.ly/plotly-latest.min.js?noext',
            },
          });
        </script>
        '''))

In [3]:
df = pd.read_pickle('FINAL2')

In [4]:
df.head()

Origin        Date Carrier Code Tail Number Destination Airport  \
0    SFO  01/01/2018           WN      N8651A                 MDW   
1    SFO  04/08/2018           WN      N8651A                 PDX   
2    SFO  06/01/2018           WN      N8651A                 PDX   
3    SFO  06/02/2018           WN      N8651A                 PHX   
4    SFO  06/18/2018           WN      N8651A                 MDW   

  Scheduled departure time Actual departure time  Departure delay (Minutes)  \
0                    05:15                 05:15                        0.0   
1                    20:30                 21:17                       47.0   
2                    06:20                 06:18                       -2.0   
3                    11:25                 11:23                       -2.0   
4                    09:25                 09:24                       -1.0   

  Wheels-off time  Taxi-Out time (Minutes)  ...  Avg_Humidity  Min_Humid  \
0           05:28                     13.0  ...          82.3         67   
1           21:44                     27.0  ...          64.6         45   
2           06:49                     31.0  ...          61.7         39   
3           11:33                     10.0  ...          58.3         33   
4           09:39                     15.0  ...          67.6         55   

   Max_Wind  Avg_Wind  Min_Wind Max_Pressure Avg_Pressure Min_Pressure  \
0         5       1.7         0         30.2         30.2         30.1   
1        26      12.0         0         30.2         30.2         30.1   
2        26      11.6         0         30.1         30.0         30.0   
3        23      10.3         0         30.0         29.9         29.9   
4        24      11.4         0         30.1         30.0         30.0   

  Num Gates   Cert_Date  
0       115  10/16/2014  
1       115  10/16/2014  
2       115  10/16/2014  
3       115  10/16/2014  
4       115  10/16/2014  

[5 rows x 32 columns]

In [5]:
df.shape

(189305, 32)

In [6]:
df.columns.tolist()

['Origin',
 'Date',
 'Carrier Code',
 'Tail Number',
 'Destination Airport',
 'Scheduled departure time',
 'Actual departure time',
 'Departure delay (Minutes)',
 'Wheels-off time',
 'Taxi-Out time (Minutes)',
 'Delay Carrier (Minutes)',
 'Delay Weather (Minutes)',
 'Delay National Aviation System (Minutes)',
 'Delay Security (Minutes)',
 'Delay Late Aircraft Arrival (Minutes)',
 'Max_Temp',
 'Avg_Temp',
 'Min_Temp',
 'Max_Dew',
 'Avg_DewPoint',
 'Min_Dew',
 'Max_Humid',
 'Avg_Humidity',
 'Min_Humid',
 'Max_Wind',
 'Avg_Wind',
 'Min_Wind',
 'Max_Pressure',
 'Avg_Pressure',
 'Min_Pressure',
 'Num Gates',
 'Cert_Date']

In [7]:
df.dtypes

Origin                                       object
Date                                         object
Carrier Code                                 object
Tail Number                                  object
Destination Airport                          object
Scheduled departure time                     object
Actual departure time                        object
Departure delay (Minutes)                   float64
Wheels-off time                              object
Taxi-Out time (Minutes)                     float64
Delay Carrier (Minutes)                     float64
Delay Weather (Minutes)                     float64
Delay National Aviation System (Minutes)    float64
Delay Security (Minutes)                    float64
Delay Late Aircraft Arrival (Minutes)       float64
Max_Temp                                     object
Avg_Temp                                     object
Min_Temp                                     object
Max_Dew                                      object
Avg_DewPoint

## **Column Definitions and Data Pre-processing**

For the sake of clarity, lets define what all these columns actually mean to get a better understanding of the date we are looking at.


**Origin** - The origin of the airport. In this case, Origin should have unique values of each airport that we chose to include in this data.  
  
**Date** - The date that this airport took off from the origin airport. 
    
**Carrier Code** - Airline code denoting which airline controls this flight  
  
**Tail Number** - Unique flight ID
  
**Destination Airport** - destination airport of this flight 
  
**Scheduled depature time** - scheduled departure time 
     
**Departure delay (Minutes)** - Delay in aircraft departure. A negative value indicates the number of minutes that an aircraft departed before its scheduled departure time.  

**Wheels-off time** - Departure time + Taxi-Out time : this is the time that the plane actually leaves the ground (takeoff)
   
**Taxi-Out time (Minutes)** - Time from leaving depature gate to actually leaving the ground  

**Delay Carrier (Minutes)** - Any aircraft delay due to delays with that specific Airline carrier  

**Delay Weather (Minutes)** - Delays resulting from weather conditions  
  
**Delay National Aviation System (Minutes)** - General nationwide delay in aviation operations  

**Delay Security (Minutes)** - Delay due to airport security issues  
   
**Delay Late Aircraft Arrival (Minutes)** - Delay due to an aircraft arriving late  

**Num_Gates** - Number of gates in that specific airport  

**Cert_Date** - The date that this specific aircraft was first certified to fly (this is a proxy for an aircraft's age)    

 


In [8]:
def get_daypart(time):
    start_times = ["05:00", "08:00", "12:00", "17:00", "21:00"]
    end_times = ["08:00", "12:00", "17:00", "21:00", "05:00"]
    day_part_list = ["Early Morning", "Morning", "Afternoon", "Evening", "Night"]
    
    for index, hour in enumerate(start_times):        
        first_time = datetime.datetime.strptime(hour,"%H:%M")
        second_time = datetime.datetime.strptime(end_times[index],"%H:%M")
        
        if time.time() >= first_time.time() and time.time() < second_time.time():
            return day_part_list[index]      
        elif index == 4:
            return day_part_list[index]

def get_day(date):    
    num = date.to_pydatetime().weekday()
    day_dict = {0 : 'Mon', 1 : 'Tues', 2 : 'Wed', 3 : 'Thurs', 4 : 'Fri', 5 : 'Sat', 6 : 'Sun'}
    return day_dict[num]

def get_month(date): 
    month_dict = {1 : 'Jan', 4 : 'Apr', 6 : 'Jun', 10 : 'Oct'}
    num = date.to_pydatetime().month
    return month_dict[num]

In [9]:
# Data Cleaning : This cell focuses on getting all the columns in the dataframe into the proper data types

df['Actual departure time'] = df['Actual departure time' ].str.replace('24', '00')

df = df[df['Cert_Date'] != 'Aircraft Description']
df = df[df['Cert_Date'] != 'None']

df['Scheduled departure time'] = df['Date'] + ' ' + df['Scheduled departure time'] 
df['Actual departure time'] = df['Date'] + ' ' + df['Actual departure time']

df['Date'] = pd.to_datetime(df['Date'], format='%m/%d/%Y')

df['Scheduled departure time'] = pd.to_datetime(df['Scheduled departure time'], format="%m/%d/%Y %H:%M")
df['Actual departure time'] = pd.to_datetime(df['Actual departure time'], format="%m/%d/%Y %H:%M") 

df['Cert_Date'] = pd.to_datetime(df['Cert_Date'], format='%m/%d/%Y')

df['Age'] = (df['Date'] - df['Cert_Date']).dt.days

df['DayOfWeek'] = df['Date'].apply(lambda row: get_day(row))
df['Month'] = df['Date'].apply(lambda row: get_month(row))

df['DayPart'] = df['Actual departure time'].apply(lambda row: get_daypart(row))

### **Handling Outliers**

Let's take a look at a boxplot of our target variable (Taxi-Out time) to identify any outliers.

In [19]:
import plotly.express as px
fig = px.box(df, y="Taxi-Out time (Minutes)")
fig.show()

In [11]:
Q1 = df["Taxi-Out time (Minutes)"].quantile(0.25)
Q3 = df["Taxi-Out time (Minutes)"].quantile(0.75)
IQR = Q3 - Q1

bound = Q3 + 1.5 * IQR
print(f'The upper bound time limit for taxi time is : {bound}')

The upper bound time limit for taxi time is : 36.0


In [18]:

fig = plotly.offline.iplot(df['Taxi-Out time (Minutes)'].iplot(asFigure=True, kind='histogram', title='Taxi-Out Time Distribution', dimensions=(600,400)))

In [17]:

month_grouped = df.groupby(['Month'])['Taxi-Out time (Minutes)'].mean()
month_grouped = month_grouped.reset_index()

fig = px.bar(month_grouped, x='Month', y='Taxi-Out time (Minutes)')

fig.update_layout(
    autosize=False,
    width=500,
    height=500,
    margin=go.layout.Margin(
        l=50,
        r=50,
        b=100,
        t=100,
        pad=4
    ),
)

fig.show()
